In [1]:
import numpy as np 
import pandas as pd
import altair as alt 
import re 
import os 
import ntpath
import sys
sys.path.append(r'../.')
from commons.data_processing import *
from modlamp.descriptors import PeptideDescriptor

In [4]:
# get all PEAKS files
files = get_files(r'E:\Research\PEAKS\20200316_PANC1_Glyco_Columns\PANC1', exts=['-peptides.csv'])
files

['E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\BP_30\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\BP_45\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\BP_60\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\C18_30\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\C18_45\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\C18_60\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\PGC_30\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\PGC_45\\protein-peptides.csv',
 'E:\\Research\\PEAKS\\20200316_PANC1_Glyco_Columns\\PANC1\\PGC_60\\protein-peptides.csv']

In [16]:
# create empty lists to store peptides
b, p, c = [], [], []

# create a blank DataFrame
df = pd.DataFrame()
# add identifier to each file and add to DF
for file in files:
    sub = pd.read_csv(file)
    source = ntpath.dirname(file)
    source = source.split('\\')[-1]
    sub['source'] = [source]*len(sub)
    if re.search('BP', file):
        sub['source_ident'] = ['BP']*len(sub)
        b.extend(sub.Peptide)
    elif re.search('C18', file):
        sub['source_ident'] = ['C18']*len(sub)
        c.extend(sub.Peptide)
    else:
        sub['source_ident'] = ['PGC']*len(sub)
        p.extend(sub.Peptide)
    if df.empty:
        df = sub
        continue
    df = pd.concat([df, sub])

In [11]:
df.head()

Protein Group  Protein ID  Protein Accession  \
0              4           3  Q09666|AHNK_HUMAN   
1              4           3  Q09666|AHNK_HUMAN   
2              4           3  Q09666|AHNK_HUMAN   
3              4           3  Q09666|AHNK_HUMAN   
4              4           3  Q09666|AHNK_HUMAN   

                           Peptide Unique  -10lgP       Mass  Length  ppm  \
0          K.GPSLDIDTPDVNIEGPEGK.L      Y   71.66  1951.9374      19  3.3   
1  K.GPFVEAEVPDVDLEC(+57.02)PDAK.L      Y   63.31  2085.9563      19  2.0   
2       K.SSGC(+57.02)DVNLPGVNVK.L      Y   63.12  1444.6980      14  2.7   
3     K.VDVEC(+57.02)PDVNIEGPEGK.W      Y   62.66  1755.7985      16  2.9   
4            R.DDGVFVQEVTQNSPAAR.T      Y   62.26  1831.8700      17  3.9   

         m/z  ...  Intensity C18_45  #Feature C18_45  Intensity C18_60  \
0   976.9792  ...               NaN              NaN               NaN   
1  1043.9875  ...               NaN              NaN               NaN   
2   723.3582  ...               NaN              NaN               NaN   
3   878.9091  ...               NaN              NaN               NaN   
4   916.9458  ...               NaN              NaN               NaN   

   #Feature C18_60  Intensity PGC_30 #Feature PGC_30  Intensity PGC_45  \
0              NaN               NaN             NaN               NaN   
1              NaN               NaN             NaN               NaN   
2              NaN               NaN             NaN               NaN   
3              NaN               NaN             NaN               NaN   
4              NaN               NaN             NaN               NaN   

   #Feature PGC_45  Intensity PGC_60  #Feature PGC_60  
0              NaN               NaN              NaN  
1              NaN               NaN              NaN  
2              NaN               NaN              NaN  
3              NaN               NaN              NaN  
4              NaN               NaN              NaN  

[5 rows x 40 columns]

In [7]:
sdf = df[['source', 'Length', 'source_ident']]

domain = sdf.source_ident.unique().tolist()
_range = ['#86858f', '#43648c', '#cc7833']

bxplt = alt.Chart(sdf, title='Average peptide Length').mark_boxplot().encode(
    x=alt.X('source:O', title='Experiment'),
    y=alt.Y('Length:Q', title='# Amino Acids'),
    color=alt.Color('source_ident:O', scale=alt.Scale(domain=domain, range=_range))
).properties(
    width=500
).configure_axis(
    labelFontSize=16,
    titleFontSize=16
).configure_title(
    fontSize=18
)

In [8]:
bxplt

alt.Chart(...)

In [8]:
bxplt.save('Average_peptide_length.svg')